In [1]:
import requests
from bs4 import BeautifulSoup
from selenium import webdriver
import pandas as pd
import itertools
import re

In [6]:
df = pd.read_csv(r'C:\Users\PutuAndika\OneDrive - Migo\Desktop\Personal Alvin\Portfolio\data-engineer\Projects\etl-project\Raw_Output.csv')
df.address.head()

Series([], Name: address, dtype: object)

In [8]:
df.head()

Empty DataFrame
Columns: [Unnamed: 0, place_name, address, bedroom, area, price, mortage, category, date_posted]
Index: []

## Preparation for Web Scarpping

In [2]:
#Define header
header = {"user-agent": "Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/106.0.0.0 Safari/537.36"}

In [3]:
#Preparing list of files
page_list = [*range(1,101)]
city_list = ['dki-jakarta','bekasi','tangerang','bogor','depok']
place_category = ['apartemen', 'rumah']
place_ownership = ['jual', 'sewa']

In [5]:
df.head()

place_name  \
0  Andre Tjhia Meruya Scandinavian House Uk 5x24 ...   
1  Andre Tjhia Tanjung Duren Rumah Baru 3 Lantai ...   
2  Rumah murah minimalis 2 lantai deket transmart...   
3          Rumah Taman Surya 3 Luas 200m2 Harga Nego   
4  Rumah Murah di Jagakarsa Jakarta Selatan Siap ...   

                         address bedroom    area           price  \
0          Meruya, Jakarta Barat       3  120 m²   Rp 2,4 Miliar   
1   Tanjung Duren, Jakarta Barat       3   33 m²  Rp 1,35 Miliar   
2  Pondok Ranggon, Jakarta Timur       3   45 m²     Rp 595 Juta   
3     Taman Surya, Jakarta Barat       4  200 m²     Rp 4 Miliar   
4     Jagakarsa, Jakarta Selatan       3   61 m²   Rp 1,2 Miliar   

                         mortage  category  \
0  Cicilan : 17 Jutaan per bulan  category   
1   Cicilan : 9 Jutaan per bulan  category   
2   Cicilan : 4 Jutaan per bulan  category   
3  Cicilan : 28 Jutaan per bulan  category   
4   Cicilan : 8 Jutaan per bulan  category   

                                         date_posted  
0  Andre Tjhia ParaLand PropertyDiperbarui sejak ...  
1  Andre Tjhia ParaLand PropertyDiperbarui sejak ...  
2          Abu Tsaqif Diperbarui sejak 05 Juni, 2023  
3            Willy KOKDiperbarui sejak 05 Juni, 2023  
4          Abdul GofarDiperbarui sejak 05 Juni, 2023

In [4]:
merged_df = pd.DataFrame()
for ownership, city, category, page in itertools.product(place_ownership,city_list, place_category, page_list):
    url = f'https://www.rumah123.com/{ownership}/{str(city)}/{category}/?page={str(page)}#qid~42eeef39-13df-4144-afa7-f1229e9827be'
    r = requests.get(url,headers=header)
    c = r.content
    page = BeautifulSoup(c, 'html.parser')
    all_city = page.find_all('div',class_='ui-organism-intersection__element intersection-card-container')
    place_name = []
    place_address = []
    building_area = []
    num_bedroom = []
    place_price = []
    place_mortage = []
    date_posted = []
    for i in all_city:
        try:
            name = i.find('a').find('h2').text
        except:
            name = None
        try:
            address = i.find('div', class_='card-featured__middle-section').find('span',text = re.compile(",")).text
        except:
            address = None
        try:
            bedroom = i.find('span', class_='attribute-text').text
        except:
            bedroom = None
        try:
            area = i.find('div', class_='attribute-info').find('span').text
        except:
            area = None
        try:
            price = i.find('div', class_='card-featured__middle-section__price').find('strong').text
        except:
            price = None
        try:
            mortage = i.find('div', class_='card-featured__middle-section__price').find('em').text.replace("Cicilan:", "").strip()
        except:
            mortage = None
        try:
            jadwal = i.find('div', class_='ui-organisms-card-r123-basic__bottom-section__agent').text
        except:
            jadwal = None
        place_name.append(name)
        place_address.append(address)
        num_bedroom.append(bedroom)
        building_area.append(area)
        place_price.append(price)
        place_mortage.append(mortage)
        date_posted.append(jadwal)
        df = pd.DataFrame({'place_name':place_name, 'address':place_address, 'bedroom':num_bedroom, 'area':building_area,
                                'price':place_price, 'mortage':place_mortage, 'category': category, 'date_posted':date_posted})
        # df.to_csv(os.path.join(path_output, f'{page}_{ownership}_{city}.csv'), index=False, sep = ';')
        merged_df = merged_df.append(df)

C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_9968\2481765341.py:54: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  merged_df = merged_df.append(df)
C:\Users\PutuAndika\AppData\Local\Temp\i

In [9]:
merged_df.to_csv('Scrap Output.csv')

In [3]:
merged_df = pd.read_csv("Scrap Output.csv")

C:\Users\PutuAndika\AppData\Local\Temp\ipykernel_17292\4055348458.py:1: DtypeWarning: Columns (6) have mixed types. Specify dtype option on import or set low_memory=False.
  merged_df = pd.read_csv("Scrap Output.csv")


## Data Cleaning

In [4]:
#Drop null values
merged_df = merged_df.dropna()

#Drop duplicated values
merged_df = merged_df.drop_duplicates(subset='place_name')

In [5]:
#Assigning kecamatan and city
merged_df[['kecamatan','city']] = merged_df.address.str.split("," ,expand = True)
merged_df = merged_df.drop(columns=['address'])
merged_df.head()

Unnamed: 0                                         place_name  bedroom  \
0            0              termurah Ci Ditiro residence low zone      3.0   
2            1  Dijual murah dan cepat 2 bedroom kosong taman ...      2.0   
5            2  Dharmawangsa Residence, Tower 1, 4 Bedroom 350...      4.0   
9            3  Apartemen Taman Anggrek Residences Studio Furn...      1.0   
14           4    Apartement The Mansion Jasmine Tower Bellavista      3.0   

      area           price                         mortage   category  \
0   132 m²  Rp 5,25 Miliar   Cicilan : 37 Jutaan per bulan  apartemen   
2    50 m²   Rp 1,5 Miliar   Cicilan : 10 Jutaan per bulan  apartemen   
5   350 m²    Rp 17 Miliar  Cicilan : 121 Jutaan per bulan  apartemen   
9    26 m²     Rp 750 Juta    Cicilan : 5 Jutaan per bulan  apartemen   
14  119 m²   Rp 3,2 Miliar   Cicilan : 22 Jutaan per bulan  apartemen   

                                      date_posted       kecamatan  \
0            Mimie Diperbarui sejak 06 Juni, 2023         Menteng   
2            Alung Diperbarui sejak 05 Juni, 2023   Taman Anggrek   
5   Margie SahuburuaDiperbarui sejak 30 Mei, 2023  Kebayoran Baru   
9        Marina ZhoDiperbarui sejak 05 Juni, 2023   Taman Anggrek   
14          Sumitro Diperbarui sejak 30 Mei, 2023      Pademangan   

                city  
0      Jakarta Pusat  
2      Jakarta Barat  
5    Jakarta Selatan  
9      Jakarta Barat  
14     Jakarta Utara